### **ANALYZING OLYMPIC DATA USING PYTHON AND SQL**

![paris-olympics-kb-2x1-220214-c2809e](paris-olympics-kb-2x1-220214-c2809e.jpg)


Get ready to explore the thrilling world of the Olympic Games through data analysis! In this Notebook, we'll use SQL and Python to dive deep into Olympics data and uncover insights that will leave you amazed.

## 🏃&nbsp;&nbsp;Load in the Olympics Data
The primary data is available in your directory in the path `athlete_events.csv`.

The cell below handles imports of the required packages and data.

In [1]:
# Import libraries
import pandas as pd
import plotly.express as px


# Import the data
olympics = pd.read_csv("athlete_events.csv")

# Preview the DataFrame
olympics

id  ... medal
0            1  ...   NaN
1            2  ...   NaN
2            3  ...   NaN
3            4  ...  Gold
4            5  ...   NaN
...        ...  ...   ...
271111  135569  ...   NaN
271112  135570  ...   NaN
271113  135570  ...   NaN
271114  135571  ...   NaN
271115  135571  ...   NaN

[271116 rows x 15 columns]

We can inspect the data types and the number of non-null rows per column using the info() method.

In [2]:
# Inspect the DataFrame
olympics.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 271116 entries, 0 to 271115
Data columns (total 15 columns):
 #   Column  Non-Null Count   Dtype  
---  ------  --------------   -----  
 0   id      271116 non-null  int64  
 1   name    271116 non-null  object 
 2   sex     271116 non-null  object 
 3   age     261642 non-null  float64
 4   height  210945 non-null  float64
 5   weight  208241 non-null  float64
 6   team    271116 non-null  object 
 7   noc     271116 non-null  object 
 8   games   271116 non-null  object 
 9   year    271116 non-null  int64  
 10  season  271116 non-null  object 
 11  city    271116 non-null  object 
 12  sport   271116 non-null  object 
 13  event   271116 non-null  object 
 14  medal   39783 non-null   object 
dtypes: float64(3), int64(2), object(10)
memory usage: 31.0+ MB


An easier way to inspect the number of missing values per column is to use isna() combined with sum().

In [3]:
# Check missing values
olympics.isna().sum()

id             0
name           0
sex            0
age         9474
height     60171
weight     62875
team           0
noc            0
games          0
year           0
season         0
city           0
sport          0
event          0
medal     231333
dtype: int64

The missing values in the `medal` column are because the dataset contains all competitors (not just those who won a medal). The remaining columns with missing values are not of interest to us today.

When exploring the data, it looked as though some of the teams had hyphens and backslashes. Let's inspect it more closely by inspecting the unique values of the column. 

By using value_counts() combined with to_frame(), we can inspect the unique team names by frequency inside the interactive table viewer.

In [4]:
# Inspect the team column
olympics["team"].value_counts().to_frame()

team
United States  17847
France         11988
Great Britain  11404
Italy          10260
Germany         9326
...              ...
Briar              1
Hannover           1
Nan-2              1
Brentina           1
Digby              1

[1184 rows x 1 columns]

The `team` column is messy and sometimes contains countries separated by forward slashes or hyphens. Let's clean this by using str.extract() to extract the first country mentioned in the cases of slashes or hyphens (e.g., "Denmark/Sweden" becomes "Denmark").


In [5]:
# Split the team column on forward slashes and hyphens
olympics["team_clean"] = olympics["team"].str.split("[/-]").str[0]

# Preview the new column
olympics["team_clean"].unique()

array(['China', 'Denmark', 'Netherlands', 'United States', 'Finland',
       'Norway', 'Romania', 'Estonia', 'France', 'Taifun', 'Morocco',
       'Spain', 'Egypt', 'Iran', 'Bulgaria', 'Italy', 'Chad',
       'Azerbaijan', 'Sudan', 'Russia', 'Argentina', 'Cuba', 'Belarus',
       'Greece', 'Cameroon', 'Turkey', 'Chile', 'Mexico', 'Soviet Union',
       'Nicaragua', 'Hungary', 'Nigeria', 'Algeria', 'Kuwait', 'Bahrain',
       'Pakistan', 'Iraq', 'United Arab Republic', 'Lebanon', 'Qatar',
       'Malaysia', 'Germany', 'Thessalonki', 'Canada', 'Ireland',
       'Australia', 'South Africa', 'Eritrea', 'Tanzania', 'Jordan',
       'Tunisia', 'Libya', 'Belgium', 'Djibouti', 'Palestine', 'Comoros',
       'Kazakhstan', 'Brunei', 'India', 'Saudi Arabia', 'Syria',
       'Maldives', 'Ethiopia', 'United Arab Emirates', 'North Yemen',
       'Indonesia', 'Philippines', 'Singapore', 'Uzbekistan',
       'Kyrgyzstan', 'Tajikistan', 'Unified Team', 'Japan',
       'Congo (Brazzaville)', 'Switzerlan

## 🌎&nbsp;&nbsp;Bring in additional data
Let's query a MariaDB database containing information on world nations to provide some additional data. 

We will store our query result as a pandas DataFrame named `nations_data`.

In [6]:
SELECT
	name AS country,
	year,
	population
From countries
INNER JOIN country_stats USING(Country_id)

country  year  population
0        Aruba  1986       62644
1        Aruba  1987       61833
2        Aruba  1988       61079
3        Aruba  1989       61032
4        Aruba  1990       62149
...        ...   ...         ...
9509  Zimbabwe  2014    13586681
9510  Zimbabwe  2015    13814629
9511  Zimbabwe  2016    14030390
9512  Zimbabwe  2017    14236745
9513  Zimbabwe  2018    14439018

[9514 rows x 3 columns]

We now have country data that we can join with the Olympics data! We will use the [`.merge()`](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.merge.html) method to combine the two DataFrames using the country and year columns.

A "left" join matches on rows in the olympics_data DataFrame, as some teams will not be present in the `countries_data` DataFrame.

In [7]:
# Perform a left join between the two DataFrames
olympics_full = olympics.merge(
    nations_data, left_on=["team_clean", "year"], right_on=["country", "year"], how="left"
)

# Preview our data
olympics_full

id                      name  ...      country    population
0            1                 A Dijiang  ...        China  1.164970e+09
1            2                  A Lamusi  ...        China  1.350695e+09
2            3       Gunnar Nielsen Aaby  ...          NaN           NaN
3            4      Edgar Lindenau Aabye  ...          NaN           NaN
4            5  Christine Jacoba Aaftink  ...  Netherlands  1.476009e+07
...        ...                       ...  ...          ...           ...
271111  135569                Andrzej ya  ...          NaN           NaN
271112  135570                  Piotr ya  ...       Poland  3.801174e+07
271113  135570                  Piotr ya  ...       Poland  3.801174e+07
271114  135571        Tomasz Ireneusz ya  ...       Poland  3.866348e+07
271115  135571        Tomasz Ireneusz ya  ...       Poland  3.823036e+07

[271116 rows x 18 columns]

## 🏆&nbsp;&nbsp;Which countries have the most gold medals?
Let's start by calculating and visualizing the number of gold medals won by athletes from different countries. To do this, we can use the query() method to filter for rows where the `medal` is "Gold" and then use group_by() to aggregate by our `team_clean` variable. We then use count() to count the number of rows per team.

A second line sorts the values of our query so that we see the top teams first!

In [8]:
# Count the number of gold medals earned by a country
gold_count = olympics_full.query("medal == 'Gold'").groupby("team_clean", as_index=False)["medal"].count()

# Sort the values
gold_count.sort_values(by="medal", ascending=False, inplace=True)

# Preview our count
gold_count

team_clean  medal
194  United States   2529
175   Soviet Union   1080
74         Germany    721
93           Italy    549
75   Great Britain    545
..             ...    ...
37          Cicely      1
177       Suriname      1
149         Panama      1
181          Syria      1
104         Kosovo      1

[208 rows x 2 columns]

We can visualize this using Plotly. Let's create a choropleth map (i.e., a world map), where the country's color is based upon the medal count!

In [9]:
# Create choropleth map of gold medal counts
fig = px.choropleth(
    gold_count,
    locations="team_clean",
    locationmode="country names",
    color="medal",
    labels={"team_clean": "Country", "Medal": "Medal_count"},
    title="Number of Gold Medals By Country"
)
fig.show()

## 📈&nbsp;&nbsp;How has the number of sports grown over time?
Another question we can ask ourselves is whether the number of individual sports has increased over time.

We will do this by grouping by the year and season (i.e., summer or winter) and then counting the number of unique using nunique().

In [10]:
# Group by year and season and count the number of unique values
sport_count = olympics_full.groupby(["year", "season"], as_index=False)["sport"].nunique()

# Preview the DataFrame
sport_count

year  season  sport
0   1896  Summer      9
1   1900  Summer     20
2   1904  Summer     18
3   1906  Summer     13
4   1908  Summer     24
5   1912  Summer     17
6   1920  Summer     25
7   1924  Summer     20
8   1924  Winter     10
9   1928  Summer     17
10  1928  Winter      8
11  1932  Summer     18
12  1932  Winter      7
13  1936  Summer     24
14  1936  Winter      8
15  1948  Summer     20
16  1948  Winter      9
17  1952  Summer     19
18  1952  Winter      8
19  1956  Summer     19
20  1956  Winter      8
21  1960  Summer     19
22  1960  Winter      8
23  1964  Summer     21
24  1964  Winter     10
25  1968  Summer     20
26  1968  Winter     10
27  1972  Summer     23
28  1972  Winter     10
29  1976  Summer     23
30  1976  Winter     10
31  1980  Summer     23
32  1980  Winter     10
33  1984  Summer     25
34  1984  Winter     10
35  1988  Summer     27
36  1988  Winter     10
37  1992  Summer     29
38  1992  Winter     12
39  1994  Winter     12
40  1996  Summer     31
41  1998  Winter     14
42  2000  Summer     34
43  2002  Winter     15
44  2004  Summer     34
45  2006  Winter     15
46  2008  Summer     34
47  2010  Winter     15
48  2012  Summer     32
49  2014  Winter     15
50  2016  Summer     34

Let's plot this data using a line plot, broken up by season!

In [11]:
# Create a line plot for Summer and Winter Olympics
fig = px.line(
    sport_count,
    x="year",
    y="sport",
    color="season",
    labels={"year": "Year", "sport": "sport_count", "season": "Season"},
    title= "Count of Disticnt Sport By Year and Season"
)

fig.show()

## 👪Which countries had the highest medal count per 10 million people in 2016?
Let's use the population data we took from our SQL database! 

To account for team data, we will first aggregate by the team, event, medal, and population and select the first medal. This will allow us to get the medals by country and event.

In [12]:
# Calculate event medals
event_medals=olympics_full.query("year == 2016")\
    .groupby(["team_clean", "event", "medal", "population"], as_index=False)["medal"].first()


# Preview the DataFrame
event_medals

team_clean                                       event  population   medal
0       Algeria                Athletics Men's 1,500 metres  40551404.0  Silver
1       Algeria                  Athletics Men's 800 metres  40551404.0  Silver
2     Argentina                         Hockey Men's Hockey  43590368.0    Gold
3     Argentina              Judo Women's Extra-Lightweight  43590368.0    Gold
4     Argentina                     Sailing Mixed Multihull  43590368.0    Gold
..          ...                                         ...         ...     ...
796  Uzbekistan  Wrestling Men's Featherweight, Greco-Roman  31847900.0  Bronze
797  Uzbekistan      Wrestling Men's Heavyweight, Freestyle  31847900.0  Bronze
798  Uzbekistan     Wrestling Men's Welterweight, Freestyle  31847900.0  Bronze
799     Vietnam        Shooting Men's Air Pistol, 10 metres  93638724.0    Gold
800     Vietnam       Shooting Men's Free Pistol, 50 metres  93638724.0  Silver

[801 rows x 4 columns]

With the event data, we can perform a similar aggregation as before and calculate the ratio of medal count to population (divided by 10 million for interpretability).

In [13]:
# Group by the team and population
medal_counts = event_medals.groupby(["team_clean", "population"], as_index=False)["medal"].count()

# Calculate the number of medals per 10000000 people
medal_counts["per_10m"] = medal_counts["medal"] / (medal_counts["population"] / 10000000)

# Sort values and take the top 20 countries
top_countries = medal_counts.sort_values(by="per_10m", ascending=False).head(20)

# Preview the DataFrame
top_countries

team_clean  population  medal    per_10m
29         Grenada    110261.0      1  90.693899
6          Bahamas    377931.0      2  52.919713
47     New Zealand   4693200.0     18  38.353362
37         Jamaica   2906238.0     11  37.849619
19         Denmark   5728010.0     15  26.187105
16         Croatia   4174349.0     10  23.955831
58        Slovenia   2065042.0      4  19.370066
26         Georgia   3727505.0      7  18.779318
5       Azerbaijan   9757812.0     18  18.446758
30         Hungary   9814023.0     15  15.284252
7          Bahrain   1425791.0      2  14.027301
41       Lithuania   2868231.0      4  13.945878
2          Armenia   2936146.0      4  13.623301
3        Australia  24190907.0     29  11.987975
46     Netherlands  17030314.0     19  11.156576
62          Sweden   9923085.0     11  11.085262
17            Cuba  11335109.0     11   9.704362
8          Belarus   9501534.0      9   9.472155
18  Czech Republic  10566332.0     10   9.464022
63     Switzerland   8373338.0      7   8.359868

We can now use a bar chart to visualize the top countries by medals per capita!

In [14]:
# Create a column chart by medal per capita
fig = px.bar(
    top_countries,
    x="team_clean",
    y="per_10m",
    labels= {"team_clean": "Country", "per_10m": "Medals per 10m"},
    title= "Number of Medals per 10 Million Population",
    hover_data=["population", "medal"]
)

fig.show()

In [15]:
olympics_full.head()

id                      name sex  ...   team_clean      country    population
0   1                 A Dijiang   M  ...        China        China  1.164970e+09
1   2                  A Lamusi   M  ...        China        China  1.350695e+09
2   3       Gunnar Nielsen Aaby   M  ...      Denmark          NaN           NaN
3   4      Edgar Lindenau Aabye   M  ...      Denmark          NaN           NaN
4   5  Christine Jacoba Aaftink   F  ...  Netherlands  Netherlands  1.476009e+07

[5 rows x 18 columns]

## Unleashing the Top 10 Athletic Powerhouses in the Olympics!

Want to know which countries dominate the world of athletics in the Olympic Games? Look no further than this code! By grouping data by country and counting the number of athletes, we've determined the top 10 countries with the highest number of athletes. From America to Australia, the results will leave you in awe of these athletic powerhouses.

In [16]:
# Group data by country and count the number of athletes
athlete_counts = olympics_full.groupby(["team_clean"], as_index=False)["name"].nunique()

# Sort the values
athlete_counts.sort_values(by="name", ascending=False, inplace=True)

athlete_counts = athlete_counts.head(10)
athlete_counts

team_clean  name
880  United States  9457
327  Great Britain  5924
289         France  5913
395          Italy  4818
318        Germany  4747
140         Canada  4704
397          Japan  4019
56       Australia  3793
809         Sweden  3636
652         Poland  2959

We can now use a bar chart to visualize the top 10 Olympic Powerhouses!

In [17]:
# Create a column chart of Number of Countries per athletes
fig = px.bar(
    athlete_counts,
    x="team_clean",
    y="name",
    labels= {"team_clean": "Country", "name": "Number of Athletes"},
    title= "Number of Athletes by Country"
)

fig.show()

## ![icons8-olympics-64](icons8-olympics-64.png) The Age of Champions: An Olympic Data Visualization

Visualize the age of champions over time with this stunning scatter plot! This chart displays the performance of Olympic athletes over the years, color-coded by the medals they won. Hover over each dot to see details about the athlete, event, and country, and witness the age-defying feats of these incredible athletes.

In [18]:
# Filter data to only include medals
medal_data = olympics_full[olympics_full["medal"].notna()]
medal_data


id                                 name  ...  country  population
3            4                 Edgar Lindenau Aabye  ...      NaN         NaN
37          15                 Arvo Ossian Aaltonen  ...      NaN         NaN
38          15                 Arvo Ossian Aaltonen  ...      NaN         NaN
40          16             Juhamatti Tapio Aaltonen  ...  Finland   5461512.0
41          17              Paavo Johannes Aaltonen  ...      NaN         NaN
...        ...                                  ...  ...      ...         ...
271078  135553  Galina Ivanovna Zybina (-Fyodorova)  ...      NaN         NaN
271080  135553  Galina Ivanovna Zybina (-Fyodorova)  ...      NaN         NaN
271082  135554                         Bogusaw Zych  ...      NaN         NaN
271102  135563            Olesya Nikolayevna Zykina  ...      NaN         NaN
271103  135563            Olesya Nikolayevna Zykina  ...      NaN         NaN

[39783 rows x 18 columns]

We can now visualize the Ages of Athletes over Time using Scatter plots!

In [19]:
# Create scatter plot of athlete performance
fig = px.scatter(
    medal_data, 
    x="year", 
    y="age", 
    color="medal", 
    hover_name="name", 
    hover_data=["event", "team_clean"], 
    labels= {"year": "Year", "age": "Age", "team_clean": "Country"},
    title="Athlete Age Over Time"
)

# Show the chart
fig.show()

## ![icons8-woman-and-man-holding-hands-48 (1)](icons8-woman-and-man-holding-hands-48%20(1).png) Breaking Down Gender Participation in the Summer Olympics

Ever wondered about the breakdown of gender participation in the Summer Olympics? Look no further than this code! By grouping data by year and gender and counting the number of unique athletes, we can see how many male and female athletes competed in each year. From the early 1900s to the present day, the results may surprise you. Get ready to uncover the gender dynamics of the Summer Olympics with this code

In [20]:
# Group data by year and gender, and count the number of unique athletes
gender_counts = olympics_full.query("season == 'Summer'").groupby(["year", "sex"], as_index=False)["name"].nunique()
gender_counts

year sex  name
0   1896   M   176
1   1900   F    23
2   1900   M  1197
3   1904   F     6
4   1904   M   644
5   1906   F     6
6   1906   M   835
7   1908   F    44
8   1908   M  1980
9   1912   F    53
10  1912   M  2356
11  1920   F    78
12  1920   M  2597
13  1924   F   156
14  1924   M  3100
15  1928   F   312
16  1928   M  2934
17  1932   F   201
18  1932   M  1721
19  1936   F   361
20  1936   M  4121
21  1948   F   446
22  1948   M  3956
23  1952   F   521
24  1952   M  4410
25  1956   F   384
26  1956   M  2962
27  1960   F   613
28  1960   M  4735
29  1964   F   680
30  1964   M  4454
31  1968   F   783
32  1968   M  4769
33  1972   F  1060
34  1972   M  6045
35  1976   F  1260
36  1976   M  4810
37  1980   F  1123
38  1980   M  4129
39  1984   F  1567
40  1984   M  5224
41  1988   F  2202
42  1988   M  6242
43  1992   F  2721
44  1992   M  6660
45  1996   F  3512
46  1996   M  6814
47  2000   F  4064
48  2000   M  6576
49  2004   F  4288
50  2004   M  6252
51  2008   F  4603
52  2008   M  6284
53  2012   F  4646
54  2012   M  5858
55  2016   F  5031
56  2016   M  6143

We can now visualize the Athlete Gender Over Time Using Stacked Bar Plots!

In [21]:
# Create stacked bar chart of gender counts over time
fig = px.bar(
    gender_counts, 
    x="year", 
    y="name", 
    color="sex", 
    barmode="stack", 
    labels= {"year": "Year", "name": "Number of Athletes"},
    title="Athlete Gender Over Time"
)

# Show the chart
fig.show()

## Wrapping up

We successfully loaded data from two different sources, performed cleaning, and then used the data to answer six questions with interactive charts.